In [5]:
!pwd

/home/cedric/code/ssaira267/fms_to_image/notebooks


In [1]:
%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt
import dlisio.dlis as dl
import pandas as pd
import numpy as np
import scipy.signal as signal
import logging
import copy

# Ensure that we can see pandas tables of up to 500 rows
# pd.set_option('display.max_rows', 500)

# Set a default DPI for all figures in this file. Lower DPI gives smaller figures, higher bigger.
mpl.rcParams['figure.dpi'] = 100

In [2]:
dl.set_encodings(['latin1'])

AttributeError: module 'dlisio.dlis' has no attribute 'set_encodings'

In [6]:
filename = '../raw_data/MESTB _009_1B.dlis'

f, *f_tail = dl.load(filename)

if len(f_tail): logging.warning('There are more logical files in tail')

In [4]:
origin, *origin_tail = f.origins

if len(origin_tail): logging.warning('f contains multiple origins')

In [7]:
f.describe()

------------
Logical File
------------
Description : LogicalFile(MESTB .009)
Frames      : 1
Channels    : 65

Known objects
--
ORIGIN      : 2
FRAME       : 1
PARAMETER   : 423
CHANNEL     : 65
TOOL        : 1
FILE-HEADER : 1


In [8]:
origin, *origin_tail = f.origins
print(len(origin_tail))

1


In [9]:
origin.describe()

------
Origin
------
name   : WELL-ODP Leg 194, Site 1196A
origin : 115
copy   : 0

Logical file ID          : MESTB .009
File set name and number : MESTB / 1
File number and type     : 0 / CUSTOMER

Well (id/name)          :  / ODP Leg 194, Site 1196A
Produced by (code/name) : 440 / Schlumberger
Produced for            : Lamont Doherty
Created                 : 2021-09-20 12:54:27

Created by              : Techlog, (version: 2017.2 (rev: 234070))
Other programs/services : WELL-ODP Leg 194, Site 1196A


In [10]:
def summarize(objs, **kwargs):
    """Create a pd.DataFrame that summarize the content of 'objs', One 
    object pr. row
    
    Parameters
    ----------
    
    objs : list()
        list of metadata objects
        
    **kwargs
        Keyword arguments 
        Use kwargs to tell summarize() which fields (attributes) of the 
        objects you want to include in the DataFrame. The parameter name 
        must match an attribute on the object in 'objs', while the value 
        of the parameters is used as a column name. Any kwargs are excepted, 
        but if the object does not have the requested attribute, 'KeyError' 
        is used as the value.
        
    Returns
    -------
    
    summary : pd.DataFrame
    """
    summary = []
    for attr, label in kwargs.items():
        column = []
        for obj in objs:
            try:
                value = getattr(obj, attr)
            except AttributeError:
                value = 'KeyError'
    
            column.append(value)
        summary.append(column)

    summary = pd.DataFrame(summary).T
    summary.columns = kwargs.values()
    return summary

In [11]:
for frame in f.frames:
    
    # Search through the channels for the index and obtain the units
    for channel in frame.channels:
        if channel.name == frame.index:
            depth_units = channel.units
    
    print(f'Frame Name: \t\t {frame.name}')
    print(f'Index Type: \t\t {frame.index_type}')
    print(f'Depth Interval: \t {frame.index_min} - {frame.index_max} {depth_units}')
    print(f'Depth Spacing: \t\t {frame.spacing} {depth_units}')
    print(f'Direction: \t\t {frame.direction}')
    print(f'Num of Channels: \t {len(frame.channels)}')
    print(f'Channel Names: \t\t {str(frame.channels)}')
    print('\n\n')

Frame Name: 		 1B
Index Type: 		 BOREHOLE-DEPTH
Depth Interval: 	 149101.0 - 322140.0 0.1 in
Depth Spacing: 		 -1.0 0.1 in
Direction: 		 DECREASING
Num of Channels: 	 65
Channel Names: 		 [Channel(TDEP), Channel(BA11), Channel(BA12), Channel(BA13), Channel(BA14), Channel(BA15), Channel(BA16), Channel(BA17), Channel(BA18), Channel(BA21), Channel(BA22), Channel(BA23), Channel(BA24), Channel(BA25), Channel(BA26), Channel(BA27), Channel(BA28), Channel(BB11), Channel(BB12), Channel(BB13), Channel(BB14), Channel(BB15), Channel(BB16), Channel(BB17), Channel(BB18), Channel(BB21), Channel(BB22), Channel(BB23), Channel(BB24), Channel(BB25), Channel(BB26), Channel(BB27), Channel(BB28), Channel(BC11), Channel(BC12), Channel(BC13), Channel(BC14), Channel(BC15), Channel(BC16), Channel(BC17), Channel(BC18), Channel(BC21), Channel(BC22), Channel(BC23), Channel(BC24), Channel(BC25), Channel(BC26), Channel(BC27), Channel(BC28), Channel(BD11), Channel(BD12), Channel(BD13), Channel(BD14), Channel(BD15), C

In [12]:
def summary_dataframe(object, **kwargs):
    # Create an empty dataframe
    df = pd.DataFrame()
    
    # Iterate over each of the keyword arguments
    for i, (key, value) in enumerate(kwargs.items()):
        list_of_values = []
        
        # Iterate over each parameter and get the relevant key
        for item in object:
            # Account for any missing values.
            try:
                x = getattr(item, key)
                list_of_values.append(x)
            except:
                list_of_values.append('')
                continue
        
        # Add a new column to our data frame
        df[value]=list_of_values
    
    # Sort the dataframe by column 1 and return it
    return df.sort_values(df.columns[0])


'1B'

In [11]:
channels = summary_dataframe(f.channels, name='Name', long_name='Long Name', dimension='Dimension', units='Units', frame='Frame')
channels

Name                   Long Name Dimension   Units      Frame
1   BA11  CALIBRATED DATA BUTTON A11       [1]          Frame(1B)
2   BA12  CALIBRATED DATA BUTTON A12       [1]          Frame(1B)
3   BA13  CALIBRATED DATA BUTTON A13       [1]          Frame(1B)
4   BA14  CALIBRATED DATA BUTTON A14       [1]          Frame(1B)
5   BA15  CALIBRATED DATA BUTTON A15       [1]          Frame(1B)
6   BA16  CALIBRATED DATA BUTTON A16       [1]          Frame(1B)
7   BA17  CALIBRATED DATA BUTTON A17       [1]          Frame(1B)
8   BA18  CALIBRATED DATA BUTTON A18       [1]          Frame(1B)
9   BA21  CALIBRATED DATA BUTTON A21       [1]          Frame(1B)
10  BA22  CALIBRATED DATA BUTTON A22       [1]          Frame(1B)
11  BA23  CALIBRATED DATA BUTTON A23       [1]          Frame(1B)
12  BA24  CALIBRATED DATA BUTTON A24       [1]          Frame(1B)
13  BA25  CALIBRATED DATA BUTTON A25       [1]          Frame(1B)
14  BA26  CALIBRATED DATA BUTTON A26       [1]          Frame(1B)
15  BA27  CALIBRATED DATA BUTTON A27       [1]          Frame(1B)
16  BA28  CALIBRATED DATA BUTTON A28       [1]          Frame(1B)
17  BB11  CALIBRATED DATA BUTTON B11       [1]          Frame(1B)
18  BB12  CALIBRATED DATA BUTTON B12       [1]          Frame(1B)
19  BB13  CALIBRATED DATA BUTTON B13       [1]          Frame(1B)
20  BB14  CALIBRATED DATA BUTTON B14       [1]          Frame(1B)
21  BB15  CALIBRATED DATA BUTTON B15       [1]          Frame(1B)
22  BB16  CALIBRATED DATA BUTTON B16       [1]          Frame(1B)
23  BB17  CALIBRATED DATA BUTTON B17       [1]          Frame(1B)
24  BB18  CALIBRATED DATA BUTTON B18       [1]          Frame(1B)
25  BB21  CALIBRATED DATA BUTTON B21       [1]          Frame(1B)
26  BB22  CALIBRATED DATA BUTTON B22       [1]          Frame(1B)
27  BB23  CALIBRATED DATA BUTTON B23       [1]          Frame(1B)
28  BB24  CALIBRATED DATA BUTTON B24       [1]          Frame(1B)
29  BB25  CALIBRATED DATA BUTTON B25       [1]          Frame(1B)
30  BB26  CALIBRATED DATA BUTTON B26       [1]          Frame(1B)
31  BB27  CALIBRATED DATA BUTTON B27       [1]          Frame(1B)
32  BB28  CALIBRATED DATA BUTTON B28       [1]          Frame(1B)
33  BC11  CALIBRATED DATA BUTTON C11       [1]          Frame(1B)
34  BC12  CALIBRATED DATA BUTTON C12       [1]          Frame(1B)
35  BC13  CALIBRATED DATA BUTTON C13       [1]          Frame(1B)
36  BC14  CALIBRATED DATA BUTTON C14       [1]          Frame(1B)
37  BC15  CALIBRATED DATA BUTTON C15       [1]          Frame(1B)
38  BC16  CALIBRATED DATA BUTTON C16       [1]          Frame(1B)
39  BC17  CALIBRATED DATA BUTTON C17       [1]          Frame(1B)
40  BC18  CALIBRATED DATA BUTTON C18       [1]          Frame(1B)
41  BC21  CALIBRATED DATA BUTTON C21       [1]          Frame(1B)
42  BC22  CALIBRATED DATA BUTTON C22       [1]          Frame(1B)
43  BC23  CALIBRATED DATA BUTTON C23       [1]          Frame(1B)
44  BC24  CALIBRATED DATA BUTTON C24       [1]          Frame(1B)
45  BC25  CALIBRATED DATA BUTTON C25       [1]          Frame(1B)
46  BC26  CALIBRATED DATA BUTTON C26       [1]          Frame(1B)
47  BC27  CALIBRATED DATA BUTTON C27       [1]          Frame(1B)
48  BC28  CALIBRATED DATA BUTTON C28       [1]          Frame(1B)
49  BD11  CALIBRATED DATA BUTTON D11       [1]          Frame(1B)
50  BD12  CALIBRATED DATA BUTTON D12       [1]          Frame(1B)
51  BD13  CALIBRATED DATA BUTTON D13       [1]          Frame(1B)
52  BD14  CALIBRATED DATA BUTTON D14       [1]          Frame(1B)
53  BD15  CALIBRATED DATA BUTTON D15       [1]          Frame(1B)
54  BD16  CALIBRATED DATA BUTTON D16       [1]          Frame(1B)
55  BD17  CALIBRATED DATA BUTTON D17       [1]          Frame(1B)
56  BD18  CALIBRATED DATA BUTTON D18       [1]          Frame(1B)
57  BD21  CALIBRATED DATA BUTTON D21       [1]          Frame(1B)
58  BD22  CALIBRATED DATA BUTTON D22       [1]          Frame(1B)
59  BD23  CALIBRATED DATA BUTTON D23       [1]          Frame(1B)
60  BD24  CALIBRATED DATA BUTTON D24       [

In [13]:
frame1 =f.object('FRAME','1B') 

In [14]:
curves = frame1.curves()

In [27]:
df = pd.DataFrame(frame1.curves())
df

FRAMENO      TDEP       BA11       BA12       BA13       BA14  \
0             1  322140.0  -0.131836  -0.136719  -0.039062  -0.161133   
1             2  322139.0  -0.131836  -0.136719  -0.039062  -0.161133   
2             3  322138.0  -0.131836  -0.136719  -0.039062  -0.161133   
3             4  322137.0  -0.131836  -0.136719  -0.039062  -0.161133   
4             5  322136.0  -0.131836  -0.136719  -0.039062  -0.161133   
...         ...       ...        ...        ...        ...        ...   
173035   173036  149105.0  27.504883  20.004883  16.250000  14.223633   
173036   173037  149104.0  27.504883  20.004883  16.250000  14.223633   
173037   173038  149103.0  27.504883  20.004883  16.250000  14.223633   
173038   173039  149102.0  27.504883  20.004883  16.250000  14.223633   
173039   173040  149101.0  27.504883  20.004883  16.250000  14.223633   

             BA15       BA16       BA17       BA18  ...      BD17      BD18  \
0       -0.180664  -0.141602  -0.117188  -0.112305  ...  0.092773  0.185547   
1       -0.180664  -0.141602  -0.117188  -0.112305  ...  0.092773  0.185547   
2       -0.180664  -0.141602  -0.117188  -0.112305  ...  0.092773  0.185547   
3       -0.180664  -0.141602  -0.117188  -0.112305  ...  0.092773  0.185547   
4       -0.180664  -0.141602  -0.117188  -0.112305  ...  0.092773  0.185547   
...           ...        ...        ...        ...  ...       ...       ...   
173035  13.520508  13.090820  13.786621  14.965820  ...  7.338867  7.587891   
173036  13.520508  13.090820  13.786621  14.965820  ...  7.338867  7.587891   
173037  13.520508  13.090820  13.786621  14.965820  ...  7.338867  7.587891   
173038  13.520508  13.090820  13.786621  14.965820  ...  7.338867  7.587891   
173039  13.520508  13.090820  13.786621  14.965820  ...  7.338867  7.587891   

            BD21      BD22      BD23      BD24      BD25      BD26      BD27  \
0      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
1      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
2      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
3      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
4      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
...          ...       ...       ...       ...       ...       ...       ...   
173035  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173036  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173037  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173038  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173039  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   

            BD28  
0       0.141602  
1       0.141602  
2       0.141602  
3       0.141602  
4       0.141602  
...          ...  
173035  7.258301  
173036  7.258301  
173037  7.258301  
173038  7.258301  
173039  7.258301  

[173040 rows x 66 columns]

In [95]:
df2 = df.drop(['FRAMENO', 'TDEP'], axis=1).describe()

BA11           BA12           BA13           BA14  \
count  173040.000000  173040.000000  173040.000000  173040.000000   
mean        6.546699       5.355473       4.729009       4.197516   
std         4.380023       3.883746       3.602724       3.447876   
min        -0.716146      -0.374349      -1.098633      -0.852864   
25%         3.435059       2.592773       2.221680       1.865234   
50%         6.245117       4.902344       4.082031       3.466797   
75%         8.977051       7.524414       6.708984       6.015625   
max        76.992188      76.872559      76.711426      75.388184   

                BA15           BA16           BA17           BA18  \
count  173040.000000  173040.000000  173040.000000  173040.000000   
mean        4.041386       4.040569       4.267269       4.518384   
std         3.456849       3.554856       3.822358       4.143742   
min        -0.621745      -0.576172      -0.480957      -0.888672   
25%         1.772461       1.777344       1.861979       1.997070   
50%         3.190918       3.125000       3.268229       3.413086   
75%         5.786133       5.766602       6.066895       6.418457   
max        75.036621      76.679688      76.906738      76.992188   

                BA21           BA22  ...           BD17           BD18  \
count  173040.000000  173040.000000  ...  173040.000000  173040.000000   
mean        5.638039       5.275983  ...       4.932242       5.617060   
std         3.942655       3.846875  ...       3.495478       3.739610   
min        -0.958659      -0.395508  ...      -0.385742      -0.576172   
25%         2.819824       2.514648  ...       2.900391       3.391113   
50%         5.273438       4.721680  ...       4.549153       5.424805   
75%         7.822266       7.426758  ...       6.325684       7.148438   
max        76.992188      76.984863  ...      71.120605      76.784668   

                BD21           BD22           BD23           BD24  \
count  173040.000000  173040.000000  173040.000000  173040.000000   
mean        4.377491       4.261262       4.197893       4.149165   
std         3.715628       3.490548       3.309515       3.260379   
min        -0.419922      -0.307617      -0.512695      -0.439453   
25%         2.165527       2.208659       2.255859       2.250977   
50%         3.671875       3.549805       3.520508       3.537598   
75%         5.722656       5.561523       5.473633       5.419922   
max        76.743164      65.297852      55.300293      54.440918   

                BD25           BD26           BD27           BD28  
count  173040.000000  173040.000000  173040.000000  173040.000000  
mean        4.408757       4.797060       5.252048       8.376035  
std         3.298164       3.441278       3.586097       4.976035  
min        -0.358887      -0.569661      -0.698242      -2.325439  
25%         2.504883       2.827148       3.193359       4.921875  
50%         3.881836       4.355469       4.970703       8.083496  
75%         5.703125       6.147461       6.687012      10.717773  
max        57.253418      63.190918      71.784668      76.870117  

[8 rows x 64 columns]

In [16]:
df["TDEP"]=df["TDEP"]* 0.00254

In [17]:
df.drop("FRAMENO", axis=1, inplace=True)
df

TDEP       BA11       BA12       BA13       BA14       BA15  \
0       818.23560  -0.131836  -0.136719  -0.039062  -0.161133  -0.180664   
1       818.23306  -0.131836  -0.136719  -0.039062  -0.161133  -0.180664   
2       818.23052  -0.131836  -0.136719  -0.039062  -0.161133  -0.180664   
3       818.22798  -0.131836  -0.136719  -0.039062  -0.161133  -0.180664   
4       818.22544  -0.131836  -0.136719  -0.039062  -0.161133  -0.180664   
...           ...        ...        ...        ...        ...        ...   
173035  378.72670  27.504883  20.004883  16.250000  14.223633  13.520508   
173036  378.72416  27.504883  20.004883  16.250000  14.223633  13.520508   
173037  378.72162  27.504883  20.004883  16.250000  14.223633  13.520508   
173038  378.71908  27.504883  20.004883  16.250000  14.223633  13.520508   
173039  378.71654  27.504883  20.004883  16.250000  14.223633  13.520508   

             BA16       BA17       BA18       BA21  ...      BD17      BD18  \
0       -0.141602  -0.117188  -0.112305  -0.136719  ...  0.092773  0.185547   
1       -0.141602  -0.117188  -0.112305  -0.136719  ...  0.092773  0.185547   
2       -0.141602  -0.117188  -0.112305  -0.136719  ...  0.092773  0.185547   
3       -0.141602  -0.117188  -0.112305  -0.136719  ...  0.092773  0.185547   
4       -0.141602  -0.117188  -0.112305  -0.136719  ...  0.092773  0.185547   
...           ...        ...        ...        ...  ...       ...       ...   
173035  13.090820  13.786621  14.965820  21.762695  ...  7.338867  7.587891   
173036  13.090820  13.786621  14.965820  21.762695  ...  7.338867  7.587891   
173037  13.090820  13.786621  14.965820  21.762695  ...  7.338867  7.587891   
173038  13.090820  13.786621  14.965820  21.762695  ...  7.338867  7.587891   
173039  13.090820  13.786621  14.965820  21.762695  ...  7.338867  7.587891   

            BD21      BD22      BD23      BD24      BD25      BD26      BD27  \
0      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
1      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
2      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
3      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
4      -0.043945 -0.014648  0.039062 -0.024414  0.068359  0.092773  0.180664   
...          ...       ...       ...       ...       ...       ...       ...   
173035  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173036  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173037  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173038  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   
173039  9.741211  8.754883  8.007812  7.519531  7.377930  7.426758  7.705078   

            BD28  
0       0.141602  
1       0.141602  
2       0.141602  
3       0.141602  
4       0.141602  
...          ...  
173035  7.258301  
173036  7.258301  
173037  7.258301  
173038  7.258301  
173039  7.258301  

[173040 rows x 65 columns]

In [18]:
cols=df.columns
cols

Index(['TDEP', 'BA11', 'BA12', 'BA13', 'BA14', 'BA15', 'BA16', 'BA17', 'BA18',
       'BA21', 'BA22', 'BA23', 'BA24', 'BA25', 'BA26', 'BA27', 'BA28', 'BB11',
       'BB12', 'BB13', 'BB14', 'BB15', 'BB16', 'BB17', 'BB18', 'BB21', 'BB22',
       'BB23', 'BB24', 'BB25', 'BB26', 'BB27', 'BB28', 'BC11', 'BC12', 'BC13',
       'BC14', 'BC15', 'BC16', 'BC17', 'BC18', 'BC21', 'BC22', 'BC23', 'BC24',
       'BC25', 'BC26', 'BC27', 'BC28', 'BD11', 'BD12', 'BD13', 'BD14', 'BD15',
       'BD16', 'BD17', 'BD18', 'BD21', 'BD22', 'BD23', 'BD24', 'BD25', 'BD26',
       'BD27', 'BD28'],
      dtype='object')

In [19]:
fmsdf = df[['BA11', 'BA12', 'BA13', 'BA14', 'BA15', 
               'BA16', 'BA17', 'BA18', 'BA21','BA22', 
               'BA23', 'BA24', 'BA25', 'BA26', 'BA27', 
               'BA28', 'BB11', 'BB12', 'BB13', 'BB14', 'BB15', 'BB16', 'BB17',
               'BB18', 'BB21', 'BB22', 'BB23', 'BB24', 'BB25', 'BB26', 'BB27', 'BB28',
               'BC11', 'BC12', 'BC13', 'BC14', 'BC15', 'BC16', 'BC17', 'BC18', 'BC21',
               'BC22', 'BC23', 'BC24', 'BC25', 'BC26', 'BC27', 'BC28', 'BD11', 'BD12',
               'BD13', 'BD14', 'BD15', 'BD16', 'BD17', 'BD18', 'BD21', 'BD22', 'BD23',
               'BD24', 'BD25', 'BD26', 'BD27', 'BD28']]

In [20]:
fms1 = ['BA11', 'BA12', 'BA13', 'BA14', 'BA15', 'BA16', 'BA17', 'BA18', 
             'BA21','BA22', 'BA23', 'BA24', 'BA25', 'BA26', 'BA27', 'BA28']

fms2 = ['BB11', 'BB12', 'BB13', 'BB14', 'BB15', 'BB16', 'BB17', 'BB18', 
             'BB21','BB22', 'BB23', 'BB24', 'BB25', 'BB26', 'BB27', 'BB28']

fms3 = ['BC11', 'BC12', 'BC13', 'BC14', 'BC15', 'BC16', 'BC17', 'BC18', 
             'BC21','BC22', 'BC23', 'BC24', 'BC25', 'BC26', 'BC27', 'BC28']


fms123 = [fms1,fms2,fms3]

In [20]:
normfms_list = []

for fms in fms123:
    fmsnorm = df[fms].copy()
    fmsnorm = ((fmsnorm-fmsnorm.min())/(fmsnorm.max()-fmsnorm.min()))*255
    normfms_list.append(fmsnorm)

allnorm = pd.concat(normfms_list,axis=1)
allnorm["TDEP"]=df["TDEP"].copy()
allnorm

BA11       BA12       BA13       BA14       BA15       BA16  \
0        1.917413   0.784441   3.472436   2.313603   1.486626   1.434395   
1        1.917413   0.784441   3.472436   2.313603   1.486626   1.434395   
2        1.917413   0.784441   3.472436   2.313603   1.486626   1.434395   
3        1.917413   0.784441   3.472436   2.313603   1.486626   1.434395   
4        1.917413   0.784441   3.472436   2.313603   1.486626   1.434395   
...           ...        ...        ...        ...        ...        ...   
173035  92.607338  67.273941  56.855133  50.425682  47.665245  45.110920   
173036  92.607338  67.273941  56.855133  50.425682  47.665245  45.110920   
173037  92.607338  67.273941  56.855133  50.425682  47.665245  45.110920   
173038  92.607338  67.273941  56.855133  50.425682  47.665245  45.110920   
173039  92.607338  67.273941  56.855133  50.425682  47.665245  45.110920   

             BA17       BA18       BA21       BA22  ...       BC18       BC21  \
0        1.198656   2.542006   2.688807   1.045906  ...   2.673699   3.033480   
1        1.198656   2.542006   2.688807   1.045906  ...   2.673699   3.033480   
2        1.198656   2.542006   2.688807   1.045906  ...   2.673699   3.033480   
3        1.198656   2.542006   2.688807   1.045906  ...   2.673699   3.033480   
4        1.198656   2.542006   2.688807   1.045906  ...   2.673699   3.033480   
...           ...        ...        ...        ...  ...        ...        ...   
173035  47.013062  51.911285  74.328201  61.805016  ...  35.893600  28.188328   
173036  47.013062  51.911285  74.328201  61.805016  ...  35.893600  28.188328   
173037  47.013062  51.911285  74.328201  61.805016  ...  35.893600  28.188328   
173038  47.013062  51.911285  74.328201  61.805016  ...  35.893600  28.188328   
173039  47.013062  51.911285  74.328201  61.805016  ...  35.893600  28.188328   

             BC22       BC23       BC24       BC25       BC26       BC27  \
0        2.751192   3.048043   3.379519   4.059012   3.607037   5.591616   
1        2.751192   3.048043   3.379519   4.059012   3.607037   5.591616   
2        2.751192   3.048043   3.379519   4.059012   3.607037   5.591616   
3        2.751192   3.048043   3.379519   4.059012   3.607037   5.591616   
4        2.751192   3.048043   3.379519   4.059012   3.607037   5.591616   
...           ...        ...        ...        ...        ...        ...   
173035  28.075769  29.850119  31.168377  32.366547  31.821009  36.488880   
173036  28.075769  29.850119  31.168377  32.366547  31.821009  36.488880   
173037  28.075769  29.850119  31.168377  32.366547  31.821009  36.488880   
173038  28.075769  29.850119  31.168377  32.366547  31.821009  36.488880   
173039  28.075769  29.850119  31.168377  32.366547  31.821009  36.488880   

             BC28       TDEP  
0       21.813217  818.23560  
1       21.813217  818.23306  
2       21.813217  818.23052  
3       21.813217  818.22798  
4       21.813217  818.22544  
...           ...        ...  
173035  52.977077  378.72670  
173036  52.977077  378.72416  
173037  52.977077  378.72162  
173038  52.977077  378.71908  
173039  52.977077  378.71654  

[173040 rows x 49 columns]

In [21]:
intervals = pd.read_csv('1196A_coreinfo.csv')
intervals = intervals.copy()
intervals

leg  site hole  core  t  sc  min_depth  max_depth  core_min  core_max  \
0    194  1196    A    10  R   1    399.575    399.610       7.5      11.0   
1    194  1196    A    10  R   1    399.620    399.660      12.0      16.0   
2    194  1196    A    10  R   1    399.720    399.750      22.0      25.0   
3    194  1196    A    10  R   1    399.770    399.800      27.0      30.0   
4    194  1196    A    10  R   1    399.850    399.880      35.0      38.0   
5    194  1196    A    10  R   1    399.890    399.920      39.0      42.0   
6    194  1196    A    10  R   1    399.980    400.010      48.0      51.0   
7    194  1196    A    10  R   1    400.150    400.180      65.0      68.0   
8    194  1196    A    10  R   1    400.200    400.230      70.0      73.0   
9    194  1196    A    10  R   1    400.250    400.280      75.0      78.0   
10   194  1196    A    10  R   1    400.300    400.340      80.0      84.0   
11   194  1196    A    10  R   1    400.355    400.380      85.5      88.0   
12   194  1196    A    10  R   1    400.400    400.430      90.0      93.0   
13   194  1196    A    10  R   1    400.450    400.490      95.0      99.0   
14   194  1196    A    10  R   1    400.510    400.540     101.0     104.0   
15   194  1196    A    10  R   1    400.715    400.745     121.5     124.5   
16   194  1196    A    10  R   1    400.765    400.795     126.5     129.5   
17   194  1196    A    11  R   1    409.430    409.485       3.0       8.5   
18   194  1196    A    11  R   1    409.555    409.600      15.5      20.0   
19   194  1196    A    11  R   1    409.635    409.670      23.5      27.0   
20   194  1196    A    11  R   1    409.685    409.725      28.5      32.5   
21   194  1196    A    11  R   1    409.745    409.780      34.5      38.0   
22   194  1196    A    11  R   1    409.830    409.885      43.0      48.5   
23   194  1196    A    11  R   1    409.945    409.975      54.5      57.5   
24   194  1196    A    11  R   1    410.060    410.090      66.0      69.0   
25   194  1196    A    12  R   1    419.015    419.045       1.5       4.5   
26   194  1196    A    12  R   1    419.260    419.290      26.0      29.0   
27   194  1196    A    12  R   1    419.330    419.365      33.0      36.5   
28   194  1196    A    12  R   1    419.385    419.425      38.5      42.5   
29   194  1196    A    12  R   1    419.485    419.530      48.5      53.0   
30   194  1196    A    12  R   1    419.670    419.710      67.0      71.0   
31   194  1196    A    12  R   1    419.740    419.780      74.0      78.0   
32   194  1196    A    12  R   1    419.915    419.945      91.5      94.5   
33   194  1196    A    12  R   1    419.960    419.990      96.0      99.0   
34   194  1196    A    12  R   1    420.090    420.130     109.0     113.0   
35   194  1196    A    12  R   1    420.235    420.270     123.5     127.0   
36   194  1196    A    13  R   1    428.785    428.820       8.5      12.0   
37   194  1196    A    13  R   1    428.940    428.970      24.0      27.0   
38   194  1196    A    13  R   1    429.105    429.135      40.5      43.5   
39   194  1196    A    13  R   1    429.170    429.200      47.0      50.0   
40   194  1196    A    13  R   1    429.320    429.350      62.0      65.0   
41   194  1196    A    13  R   1    429.370    429.400      67.0      70.0   
42   194  1196    A    13  R   1    429.440    429.470      74.0      77.0   
43   194  1196    A    13  R   1    429.540    429.590      84.0      89.0   
44   194  1196    A    13  R   1    429.620    429.655      92.0      95.5   
45   194  1196    A    13  R   1    429.740    429.770     104.0     107.0   
46   194  1196    A    13  R   1    429.820    429.860     112.0     116.0   
47   194  1196    A    13  R   1    429.925    429.965     122.5     126.5   
48   194  1196    A    13  R   1    429.995    430.035     129.5     133.5   
49   194  1196    A    13  R   1    430.080    430.135     138.0     143.5   
50   194  1196    A    13  

In [71]:
for index, interval in intervals.iterrows():
    min_depth = interval.min_depth
    max_depth = interval.max_depth
    print(allnorm[(allnorm['TDEP']>=min_depth) & (allnorm['TDEP']<=max_depth)])

             BA11       BA12       BA13       BA14       BA15       BA16  \
164814  26.528671  24.833492  26.723354  25.912363  25.629190  25.625711   
164815  26.833107  25.075270  26.931379  26.173664  25.859591  25.819113   
164816  27.153566  25.429882  27.283422  26.516623  26.221645  26.189798   
164817  27.393911  25.703899  27.523455  26.794254  26.435589  26.399317   
164818  27.650278  25.913441  27.795488  26.990231  26.649530  26.560486   
164819  27.794485  25.994034  27.827492  27.022894  26.698902  26.608835   
164820  27.834541  26.050449  27.827492  27.047392  26.690672  26.600777   
164821  27.882610  26.114925  27.907501  27.063723  26.707130  26.633011   
164822  27.866589  26.098806  27.907501  27.096384  26.740046  26.633011   
164823  27.930681  26.163280  27.971510  27.129047  26.740046  26.665243   
164824  28.106932  26.292231  28.083523  27.259697  26.888159  26.794178   
164825  28.074886  26.292231  28.099525  27.259697  26.871702  26.778061   
164826  28.0

             BA11       BA12       BA13       BA14       BA15       BA16  \
160688  30.854870  26.574306  26.131279  23.005388  20.017321  17.019341   
160689  30.854870  26.558189  26.083273  22.972725  20.000862  17.019341   
160690  30.822823  26.574306  26.099276  22.989058  20.000862  16.987106   
160691  30.854870  26.558189  26.083273  23.005388  20.017321  17.035458   
160692  30.854870  26.558189  26.099276  22.972725  20.033777  17.035458   
160693  30.838846  26.542070  26.067272  22.940063  20.017321  17.051573   
160694  30.870892  26.574306  26.099276  22.940063  20.000862  17.083807   
160695  30.822823  26.542070  26.043268  22.891069  20.000862  17.132158   
160696  30.806801  26.542070  26.043268  22.874739  19.935034  17.132158   
160697  30.790777  26.493713  25.963259  22.793081  19.836292  17.067690   
160698  30.806801  26.477594  25.931255  22.760420  19.754005  16.874289   
160699  30.774755  26.461475  25.915251  22.727757  19.671721  16.680889   

           

             BA11       BA12       BA13       BA14       BA15       BA16  \
152835  31.271467  23.060438  19.442440  17.240431  18.634924  18.582668   
152836  35.437435  26.638783  23.010887  20.963972  24.312622  23.417709   
152837  36.046307  25.413765  19.906498  12.259378  12.710367  11.990899   
152838  35.052883  23.866371  16.226036   7.376313   6.785812   5.673113   
152839  34.716400  24.301575  20.850616  14.366119  10.175974   5.028441   
152840  34.187645  23.221626  20.210537  13.631209  11.179857   9.508912   
152841  34.828564  22.609116  15.954002  11.165179  13.236995  13.747630   
152842  33.963322  21.658113  15.089893  13.255589  17.812069  20.355516   
152843  30.181906  17.805754  11.537448  10.756897  23.325197  28.784603   
152844  27.730392  16.193886  10.609331   9.842343  19.967947  25.448425   
152845  27.089476  16.661327  12.705595  11.965414  15.705560  19.195108   
152846  27.666302  17.886345  18.370306  19.967764  18.272865  14.956389   
152847  30.1

             BA11       BA12       BA13       BA14       BA15       BA16  \
149207  54.512760  46.231022  43.637478  39.949139  38.062527  37.463501   
149208  54.384579  46.231022  43.893509  40.275764  38.556244  38.092056   
149209  54.384579  46.359970  44.149544  40.863689  38.967670  38.688377   
149210  54.384579  46.359970  44.277557  41.124992  39.412010  39.284698   
149211  54.512760  46.617870  44.533588  41.386292  39.856354  40.058304   
149212  54.512760  46.746819  44.789623  41.778244  40.531094  40.574043   
149213  54.512760  46.875767  44.917637  41.908894  40.794407  40.960846   
149214  54.769127  47.262615  45.429703  42.692799  41.584351  41.734451   
149215  55.025494  47.520515  45.813751  43.084747  41.979321  42.250191   
149216  55.538231  48.036312  46.325813  43.476700  42.505943  42.765926   
149217  55.538231  48.036312  46.453831  43.738003  42.769260  43.023796   
149218  55.538231  48.165260  46.453831  43.868652  43.032574  43.281666   

           

             BA11       BA12       BA13       BA14       BA15       BA16  \
134005  30.918962  20.707113  16.834114  13.582215  12.282483  14.021615   
134006  31.239422  21.029486  17.058142  13.876179  13.236995  13.167425   
134007  31.351582  21.239029  17.762228  13.843517  12.660995  11.007773   
134008  31.207375  21.190672  18.434313  13.941504  11.377342   9.976299   
134009  30.710663  20.997248  18.690346  14.921384  10.998829  10.717671   
134010  30.302078  20.344442  19.010386  16.970964  11.533685  14.803280   
134011  30.430260  20.586222  19.858492  18.816404  13.047738  16.592245   
134012  30.718674  21.440512  20.194534  17.264929  13.146481  13.723454   
134013  31.007088  22.069139  20.002510  14.945881  12.702139  12.095658   
134014  31.199364  21.537224  18.658342  13.329080  11.533685   9.984358   
134015  31.936420  21.166494  17.490196  12.741153  11.007057   8.340445   

             BA17       BA18       BA21       BA22  ...       BC18       BC21  \
134005

...

            BA11       BA12       BA13       BA14       BA15       BA16  \
62385  28.675749  24.333813  23.923002  20.408709  16.133444  10.089116   
62386  30.710663  25.929560  25.443193  21.862196  17.943724  11.926432   
62387  30.213951  24.092033  22.066769  16.979130  14.504191  10.943306   
62388  27.009361  18.853466  13.729723   8.356193  10.850715   9.379977   
62389  16.866829   8.859893   6.624832   3.701765   6.127527   8.719189   
62390   7.845906   6.974009   9.505193   8.290867   5.699643   4.835040   
62391   9.175811  12.035270  15.601958  11.851096   6.061699   5.044558   
62392   8.390687   8.070078  12.977629  16.080908  16.067616  11.007773   
62393   5.682807   7.151314  14.801858  21.372257  20.873089   9.122108   
62394  10.073097   8.601994  15.841989  18.432619  16.215729   6.237201   
62395  11.018451   6.087482  10.561325  10.054650   9.435405   5.785931   

           BA17      BA18       BA21       BA22  ...       BC18       BC21  \
62385  4.239542  3.22

            BA11       BA12       BA13       BA14       BA15       BA16  \
20507  23.532379  19.546570  19.741144  17.289425  15.442246  13.828215   
20508  23.740677  19.723873  19.901163  17.452740  15.458703  13.634812   
20509  23.981022  19.981773  20.125191  17.583389  15.606817  13.650929   
20510  24.269434  20.255789  20.493237  17.926348  15.837215  13.699280   
20511  24.477734  20.449215  20.573248  18.056997  15.886587  13.650929   
20512  24.718079  20.594282  20.685261  18.122324  15.952416  13.715396   
20513  24.910355  20.803825  20.877287  18.220310  16.001787  13.924914   
20514  25.070583  20.900537  20.909290  18.220310  16.051157  13.989382   
20515  25.118650  20.965012  20.957294  18.285637  16.116987  14.150550   
20516  25.182743  20.981131  21.005301  18.399956  16.363842  14.601820   
20517  25.214790  21.045605  21.053308  18.465281  16.462585  14.827456   
20518  25.230814  21.093960  21.037306  18.497944  16.610701  15.085324   
20519  25.375019  21.2229

          BA11      BA12      BA13      BA14      BA15      BA16      BA17  \
8995  8.534893  0.977865  3.397761  2.313603  1.568911  1.788965  1.879773   
8996  8.631031  0.961746  3.413763  2.329934  1.535997  1.837315  1.879773   
8997  8.615008  0.961746  3.365757  2.346266  1.568911  1.788965  1.895862   
8998  8.631031  0.929509  3.397761  2.297272  1.585368  1.821198  1.895862   
8999  8.615008  0.945627  3.381759  2.297272  1.535997  1.788965  1.863683   
9000  8.663076  0.961746  3.392426  2.329934  1.568911  1.805081  1.895862   
9001  8.695123  0.977865  3.392426  2.346266  1.585368  1.853432  1.895862   
9002  8.759215  0.993983  3.360422  2.313603  1.568911  1.821198  1.911951   
9003  8.743191  0.961746  3.360422  2.346266  1.552454  1.821198  1.879773   
9004  8.631031  0.961746  3.344420  2.313603  1.552454  1.837315  1.879773   
9005  8.711145  0.977865  3.360422  2.297272  1.568911  1.805081  1.895862   
9006  8.759215  0.945627  3.376424  2.329934  1.535997  1.805081

          BA11       BA12       BA13       BA14      BA15      BA16      BA17  \
8223  6.692253   7.828298   9.190488   7.964241  3.082964  3.094425  2.646697   
8224  6.676230   7.876654   9.174486   7.980572  3.115878  3.110542  2.678876   
8225  6.676230   7.892773   9.126479   7.996903  3.099422  3.110542  2.646697   
8226  6.756345   7.941129   8.998464   8.029566  3.115878  3.175009  2.759322   
8227  6.788391   7.973366   8.966459   8.013234  3.115878  3.142776  2.807590   
8228  6.820437   8.021722   8.982462   8.045897  3.132336  3.158893  2.775412   
8229  6.836460   7.989484   9.030467   8.029566  3.148793  3.158893  2.775412   
8230  6.836460   7.957248   9.078474   7.980572  3.115878  3.142776  2.694965   
8231  6.756345   7.941129   9.174486   7.996903  3.115878  3.110542  2.694965   
8232  6.756345   7.941129   9.142482   7.947909  3.082964  3.110542  2.630608   
8233  6.708276   7.941129   9.190488   7.980572  3.132336  3.078309  2.614518   
8234  6.676230   7.957248   

           BA11       BA12       BA13       BA14      BA15       BA16  \
5548  12.668816  12.470474  11.665464  13.467896  9.797461  16.342434   
5549  12.764954  12.454355  11.649462  13.516891  9.781004  16.326319   
5550  12.722226  12.411373  11.633459  13.440679  9.786490  16.331692   
5551  12.658134  12.443610  11.601456  13.440679  9.770033  16.267223   
5552  12.722226  12.411373  11.585454  13.408015  9.770033  16.267223   
5553  12.658134  12.395255  11.585454  13.375354  9.737119  16.267223   
5554  12.658134  12.411373  11.569452  13.391685  9.753576  16.218872   
5555  12.642112  12.346899  11.569452  13.359022  9.753576  16.202757   
5556  12.610066  12.330780  11.569452  13.342690  9.687748  16.170523   
5557  12.610066  12.427491  11.537448  13.228371  9.687748  16.251106   
5558  12.610066  12.604797  11.473439  13.114052  9.638376  16.380041   
5559  12.481882  12.927171  11.409432  12.836420  9.572548  16.654028   
5560  12.225515  13.926528  11.201406  11.970860  9

In [85]:
for index, interval in intervals.iterrows():
    min_depth = interval.min_depth
    max_depth = interval.max_depth
    allnorm_intervals = allnorm[(allnorm['TDEP']>=min_depth) & (allnorm['TDEP']<=max_depth)]
    print (allnorm_intervals)

             BA11       BA12       BA13       BA14       BA15       BA16  \
164814  26.528671  24.833492  26.723354  25.912363  25.629190  25.625711   
164815  26.833107  25.075270  26.931379  26.173664  25.859591  25.819113   
164816  27.153566  25.429882  27.283422  26.516623  26.221645  26.189798   
164817  27.393911  25.703899  27.523455  26.794254  26.435589  26.399317   
164818  27.650278  25.913441  27.795488  26.990231  26.649530  26.560486   
164819  27.794485  25.994034  27.827492  27.022894  26.698902  26.608835   
164820  27.834541  26.050449  27.827492  27.047392  26.690672  26.600777   
164821  27.882610  26.114925  27.907501  27.063723  26.707130  26.633011   
164822  27.866589  26.098806  27.907501  27.096384  26.740046  26.633011   
164823  27.930681  26.163280  27.971510  27.129047  26.740046  26.665243   
164824  28.106932  26.292231  28.083523  27.259697  26.888159  26.794178   
164825  28.074886  26.292231  28.099525  27.259697  26.871702  26.778061   
164826  28.0

             BA11       BA12       BA13       BA14       BA15       BA16  \
160688  30.854870  26.574306  26.131279  23.005388  20.017321  17.019341   
160689  30.854870  26.558189  26.083273  22.972725  20.000862  17.019341   
160690  30.822823  26.574306  26.099276  22.989058  20.000862  16.987106   
160691  30.854870  26.558189  26.083273  23.005388  20.017321  17.035458   
160692  30.854870  26.558189  26.099276  22.972725  20.033777  17.035458   
160693  30.838846  26.542070  26.067272  22.940063  20.017321  17.051573   
160694  30.870892  26.574306  26.099276  22.940063  20.000862  17.083807   
160695  30.822823  26.542070  26.043268  22.891069  20.000862  17.132158   
160696  30.806801  26.542070  26.043268  22.874739  19.935034  17.132158   
160697  30.790777  26.493713  25.963259  22.793081  19.836292  17.067690   
160698  30.806801  26.477594  25.931255  22.760420  19.754005  16.874289   
160699  30.774755  26.461475  25.915251  22.727757  19.671721  16.680889   

           

             BA11       BA12       BA13       BA14       BA15       BA16  \
152796  24.069149  15.218707  16.994133  12.708489  10.315860   7.937524   
152797  25.575306  16.862812  20.066519  18.571436  15.170704   9.645904   
152798  27.337831  18.345728  21.074644  21.102789  15.532760  10.886898   
152799  28.843988  19.038832  18.354303  16.611675  10.891858   7.566837   
152800  29.484907  18.893763  14.529823   8.756310   6.037014   9.371919   
152801  29.244562  17.926641  12.321547   5.914660   5.411644  15.077266   
152802  28.539553  16.637150  11.201406   7.025189   9.427176  20.847080   
152803  28.715805  17.346371  11.185404   9.164593  12.208426  19.944538   
152804  30.302078  19.538509  12.113520   9.115599  13.031281  17.494785   
152805  31.319536  20.529808  13.857738  10.887547  14.257335  25.706295   
152806  32.280914  22.415691  15.681968  14.251800  15.359961  31.959614   
152807  32.809669  25.107508  16.370054  10.789559  17.170240  24.868221   
152808  31.8

             BA11       BA12       BA13       BA14       BA15       BA16  \
149207  54.512760  46.231022  43.637478  39.949139  38.062527  37.463501   
149208  54.384579  46.231022  43.893509  40.275764  38.556244  38.092056   
149209  54.384579  46.359970  44.149544  40.863689  38.967670  38.688377   
149210  54.384579  46.359970  44.277557  41.124992  39.412010  39.284698   
149211  54.512760  46.617870  44.533588  41.386292  39.856354  40.058304   
149212  54.512760  46.746819  44.789623  41.778244  40.531094  40.574043   
149213  54.512760  46.875767  44.917637  41.908894  40.794407  40.960846   
149214  54.769127  47.262615  45.429703  42.692799  41.584351  41.734451   
149215  55.025494  47.520515  45.813751  43.084747  41.979321  42.250191   
149216  55.538231  48.036312  46.325813  43.476700  42.505943  42.765926   
149217  55.538231  48.036312  46.453831  43.738003  42.769260  43.023796   
149218  55.538231  48.165260  46.453831  43.868652  43.032574  43.281666   

           

             BA11      BA12      BA13      BA14      BA15      BA16      BA17  \
134095  11.435048  5.555566  5.360672  3.195494  1.437254  0.805840  0.571172   
134096  11.050497  5.136481  5.168648  3.146501  1.700568  1.095942  0.699886   
134097  11.130611  4.910820  4.912616  2.803543  1.486626  1.015358  1.777872   
134098  11.611300  5.023650  4.912616  2.672892  1.058741  1.192643  1.777872   
134099  12.156080  5.491092  5.024631  2.280941  1.322055  1.386045  1.214745   
134100  13.005298  6.055245  5.184651  2.117627  2.062624  0.725256  1.134299   
134101  13.053367  6.039126  4.976624  2.493248  1.898053  0.983125  1.037763   
134102  11.563231  4.991413  4.240532  2.852537  0.778970  0.628555  0.651618   
134103  10.297418  4.201598  4.048508  2.378928  0.713142  0.660789  0.651618   
134104   9.047628  3.508495  3.760472  1.595025  0.713142  0.821957  0.667708   
134105   8.214435  3.186122  3.536444  1.350055  0.614399  0.789723  0.876869   
134106   7.557493  2.976579 

...

            BA11       BA12       BA13       BA14       BA15       BA16  \
66172  31.688063  21.480808  18.018261  13.320914  11.377342  12.506637   
66173  31.127260  21.222910  17.970257  13.124938  10.801344  13.489760   
66174  30.374182  20.626518  17.554203  12.634998  10.570945  15.407660   
66175  29.557011  19.965654  16.834114  12.128728  10.883630  16.987106   
66176  28.275173  19.095247  16.050014  12.030740  10.982372  16.987106   
66177  27.890623  18.434380  15.441938  11.785769  10.488659  15.036974   
66178  27.249704  17.870226  15.105896  11.312162  10.027861  12.168184   
66179  26.560717  17.451141  14.993881  11.426481   9.879746   9.879598   
66180  25.967869  17.144888  14.905870  11.540801  10.603858   8.848123   
66181  25.310926  16.629089  14.329799  11.328493  12.068540   8.928707   
66182  24.445688  15.823156  13.161652  11.099854  13.385109   9.251042   
66183  23.356127  14.743206  11.593455  10.969204  14.076306   9.122108   
66184  22.250542  13.6471

            BA11       BA12       BA13       BA14       BA15       BA16  \
20784  26.368443  21.593639  21.026640  17.763035  15.162476  12.957907   
20785  26.352421  21.577520  21.026640  17.763035  15.129560  12.941791   
20786  26.384466  21.609758  21.026640  17.763035  15.129560  12.925673   
20787  26.352421  21.625877  21.058643  17.828360  15.228303  12.990141   
20788  26.368443  21.641994  21.090647  17.893684  15.228303  13.006257   
20789  26.384466  21.674232  21.106649  17.893684  15.294132  13.006257   
20790  26.384466  21.480808  21.106649  17.926348  15.310589  12.957907   
20791  26.336397  21.577520  21.090647  17.910015  15.294132  12.957907   
20792  26.336397  21.641994  21.122650  17.959011  15.327045  12.974024   
20793  26.336397  21.641994  21.138653  17.959011  15.359961  13.022374   
20794  26.304350  21.641994  21.106649  17.959011  15.376417  13.086841   
20795  26.352421  21.593639  21.090647  17.959011  15.376417  13.119075   

            BA17       B

          BA11      BA12       BA13      BA14       BA15       BA16  \
9162  2.574354  1.364713   3.472436  2.150290   1.354969   1.224877   
9163  4.304833  1.364713   3.520442  2.852537   1.930967   1.869549   
9164  4.192672  1.509781   4.288538  3.113838   1.881596   1.917899   
9165  7.893975  2.847630   5.125978  3.293482   1.799311   2.884907   
9166  3.711983  1.832154   4.133853  2.117627   1.371426   1.160410   
9167  3.824144  1.122933   3.381759  2.150290   1.354969   1.192643   
9168  2.766629  0.961746   3.301749  2.150290   1.371426   1.934016   
9169  2.029573  0.655491   3.317751  2.264609   2.029710   3.271710   
9170  1.612976  0.848915   4.805937  5.318566   3.642506   2.772089   
9171  1.645022  0.832797   4.341879  7.245663   1.667654   2.369169   
9172  1.709114  1.171289   5.029965  7.572289   2.408223   3.400645   
9173  1.773206  1.461425   5.414013  6.494421   3.626049   3.481229   
9174  1.997527  0.929509   6.662170  4.812295   3.905819   3.416761   
9175  

          BA11      BA12      BA13      BA14      BA15      BA16      BA17  \
8326  2.125711  0.639373  3.136394  2.117627  1.387883  1.224877  0.887594   
8327  2.109688  0.574898  3.136394  2.182952  1.354969  1.176526  0.887594   
8328  2.141734  0.558779  3.152396  2.182952  1.404340  1.192643  0.871505   
8329  2.109688  0.542661  3.168397  2.166621  1.420797  1.192643  0.855416   
8330  2.077642  0.542661  3.120392  2.182952  1.387883  1.208760  0.871505   
8331  2.077642  0.574898  3.152396  2.117627  1.371426  1.257110  0.871505   
8332  2.093665  0.558779  3.136394  2.084965  1.354969  1.257110  0.855416   
8333  2.077642  0.574898  3.152396  2.133958  1.338512  1.176526  0.774969   
8334  2.061619  0.591017  3.104389  2.101296  1.371426  1.176526  1.064577   
8335  2.029573  0.542661  3.184400  2.133958  1.437254  1.192643  2.078206   
8336  2.029573  0.526542  3.232406  2.150290  1.338512  1.192643  2.190831   
8337  2.077642  0.558779  3.216404  2.084965  1.338512  1.450512

           BA11       BA12       BA13       BA14       BA15       BA16  \
5617   1.842640   0.757577   3.296414   2.139403   1.343999   1.165783   
5618   1.858663   0.709221   3.312416   2.155735   1.590855   1.504236   
5619   1.858663   0.676984   3.456434   2.139403   1.327542   1.439769   
5620   1.970824   0.789815   3.344420   2.057747   1.936454   1.488119   
5621  27.190956  26.676392  26.563334  25.215563  20.944405  16.154406   
5622  42.076283  41.844059  40.853127  37.774349  33.468254  29.209013   
5623  49.510933  50.612610  51.446457  49.745209  47.111191  42.376438   
5624  52.074604  55.125839  59.255436  61.634411  62.778358  60.169388   
5625  49.639114  51.773155  59.127419  61.634411  63.436638  63.650616   
5626  47.331810  51.128410  57.079163  59.805302  62.120075  62.877010   
5627  43.101749  47.002029  53.110664  56.408386  58.828651  60.040451   
5628  38.326908  42.746704  49.526215  53.534073  56.722145  58.622173   
5629  37.397579  41.715107  48.502087 

In [92]:
def open_fms(filename:str) -> pd.DataFrame:
    f, *f_tail = dl.load(filename)
    if len(f_tail): logging.warning('There are more logical files in tail')
    
    frame =f.object('FRAME','1B').curves()
    
    df = pd.DataFrame(frame)
    df["TDEP"]=df["TDEP"]* 0.00254
    df.drop(["FRAMENO"], axis=1, inplace=True)
    
    
    cols_list = [['TDEP','BA11', 'BA12', 'BA13', 'BA14', 'BA15', 'BA16', 'BA17', 'BA18', 
             'BA21','BA22', 'BA23', 'BA24', 'BA25', 'BA26', 'BA27', 'BA28'],
            ['TDEP','BB11', 'BB12', 'BB13', 'BB14', 'BB15', 'BB16', 'BB17', 'BB18', 
             'BB21','BB22', 'BB23', 'BB24', 'BB25', 'BB26', 'BB27', 'BB28'],
            ['TDEP','BC11', 'BC12', 'BC13', 'BC14', 'BC15', 'BC16', 'BC17', 'BC18', 
             'BC21','BC22', 'BC23', 'BC24', 'BC25', 'BC26', 'BC27', 'BC28']]

    
    pads = [df[cols].copy() for cols in cols_list]
    pads_norm = [normalize_values(pad) for pad in pads]
    
    return pads_norm

def normalize_values(data:pd.DataFrame) -> pd.DataFrame:
    TDEP= data['TDEP'].copy()
    data.drop(['TDEP'], axis=1, inplace=True)
    data = (data-data.min())/(data.max()-data.min())
    data['TDEP'] = TDEP    
    
    return data

def get_core_info(filename:str):
    data = pd.read_csv(filename)
    data['max_depth'] = data['min_depth']+data['core_v_pixel']/20000
    print((data['core_v_pixel']-data['core_v_pixel']%512)/512)
    return data
    
def slice_images(image:df.DataFrame)
    
     

In [93]:
get_core_info('../raw_data/1196A_coreinfo.csv')

0      1.0
1      1.0
2      1.0
3      1.0
4      1.0
      ... 
372    1.0
373    1.0
374    3.0
375    7.0
376    3.0
Name: core_v_pixel, Length: 377, dtype: float64


leg  site hole  core  t  sc  min_depth  max_depth  core_min  core_max  \
0    194  1196    A    10  R   1    399.575  399.61025       7.5      11.0   
1    194  1196    A    10  R   1    399.620  399.65985      12.0      16.0   
2    194  1196    A    10  R   1    399.720  399.75025      22.0      25.0   
3    194  1196    A    10  R   1    399.770  399.79695      27.0      30.0   
4    194  1196    A    10  R   1    399.850  399.88005      35.0      38.0   
..   ...   ...  ...   ... ..  ..        ...        ...       ...       ...   
372  194  1196    A    52  R   2    805.305  805.35505      13.5      18.5   
373  194  1196    A    52  R   2    805.375  805.40130      20.5      23.0   
374  194  1196    A    52  R   2    805.425  805.50495      25.5      33.5   
375  194  1196    A    52  R   2    805.515  805.70045      34.5      53.0   
376  194  1196    A    52  R   2    805.770  805.85495      60.0      68.5   

     core_v_pixel  
0             705  
1             797  
2             605  
3             539  
4             601  
..            ...  
372          1001  
373           526  
374          1599  
375          3709  
376          1699  

[377 rows x 11 columns]

In [66]:
open_fms('../raw_data/MESTB _009_1B.dlis')[1]

BB11      BB12      BB13      BB14      BB15      BB16      BB17  \
0       0.013184  0.008100  0.007925  0.010181  0.013033  0.010375  0.007724   
1       0.013184  0.008100  0.007925  0.010181  0.013033  0.010375  0.007724   
2       0.013184  0.008100  0.007925  0.010181  0.013033  0.010375  0.007724   
3       0.013184  0.008100  0.007925  0.010181  0.013033  0.010375  0.007724   
4       0.013184  0.008100  0.007925  0.010181  0.013033  0.010375  0.007724   
...          ...       ...       ...       ...       ...       ...       ...   
173035  0.179729  0.187826  0.205972  0.219675  0.240293  0.253749  0.259799   
173036  0.179729  0.187826  0.205972  0.219675  0.240293  0.253749  0.259799   
173037  0.179729  0.187826  0.205972  0.219675  0.240293  0.253749  0.259799   
173038  0.179729  0.187826  0.205972  0.219675  0.240293  0.253749  0.259799   
173039  0.179729  0.187826  0.205972  0.219675  0.240293  0.253749  0.259799   

            BB18      BB21      BB22      BB23      BB24      BB25      BB26  \
0       0.009518  0.010607  0.009825  0.008135  0.011313  0.010112  0.006812   
1       0.009518  0.010607  0.009825  0.008135  0.011313  0.010112  0.006812   
2       0.009518  0.010607  0.009825  0.008135  0.011313  0.010112  0.006812   
3       0.009518  0.010607  0.009825  0.008135  0.011313  0.010112  0.006812   
4       0.009518  0.010607  0.009825  0.008135  0.011313  0.010112  0.006812   
...          ...       ...       ...       ...       ...       ...       ...   
173035  0.281127  0.181828  0.196953  0.210852  0.228611  0.230176  0.223145   
173036  0.281127  0.181828  0.196953  0.210852  0.228611  0.230176  0.223145   
173037  0.281127  0.181828  0.196953  0.210852  0.228611  0.230176  0.223145   
173038  0.281127  0.181828  0.196953  0.210852  0.228611  0.230176  0.223145   
173039  0.281127  0.181828  0.196953  0.210852  0.228611  0.230176  0.223145   

            BB27      BB28       TDEP  
0       0.005880  0.005417  818.23560  
1       0.005880  0.005417  818.23306  
2       0.005880  0.005417  818.23052  
3       0.005880  0.005417  818.22798  
4       0.005880  0.005417  818.22544  
...          ...       ...        ...  
173035  0.238223  0.324379  378.72670  
173036  0.238223  0.324379  378.72416  
173037  0.238223  0.324379  378.72162  
173038  0.238223  0.324379  378.71908  
173039  0.238223  0.324379  378.71654  

[173040 rows x 17 columns]